In [1]:
# !pip install jiwer
# # !pip install --upgrade pip

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 0.0/2.2 MB ? eta -:--:--


     ━━━━━━╸━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 0.4/2.2 MB 10.9 MB/s eta 0:00:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╸ 2.2/2.2 MB 33.3 MB/s eta 0:00:01


     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.2/2.2 MB 25.0 MB/s eta 0:00:00


  Attempting uninstall: rapidfuzz
    Found existing installation: rapidfuzz 3.1.1
    Uninstalling rapidfuzz-3.1.1:


      Successfully uninstalled rapidfuzz-3.1.1


In [2]:
# # %cd "/content/drive/MyDrive/Urdu_Speech_wavs"
# %cd "/kaggle/working/"

/kaggle/working


In [3]:

# !unzip "limited_wav_files.zip" -d "/dataset"

In [4]:
# import os
# print(len(os.listdir("/kaggle/input/urdu-dataset-20000/limited_wav_files/limited_wav_files")))

20000


In [5]:
# import os
# from tensorflow import keras
# keras.utils.get_file(
#     os.path.join(os.getcwd(), "cv-corpus-14.0-2023-06-23-ur.tar.gz"),
#     "https://commonvoice.mozilla.org/en/datasets",
#     extract=True,
#     archive_format="tar",
#     cache_dir=".",
# )


In [1]:
import pandas as pd
import numpy as np
import tensorflow as tf
from tensorflow import keras
from tensorflow.keras import layers
import matplotlib.pyplot as plt
from IPython import display
from jiwer import wer


In [6]:

data_path = '../'#if path not  changed then /content/drive/MyDrive/Urdu_Speech_wavs/

wavs_path = data_path + "Dataset/cv-corpus-14.0-2023-06-23/ur/limited_wav_files/limited_wav_files/"
metadata_path = data_path + "Dataset/cv-corpus-14.0-2023-06-23/ur/final_main_dataset.tsv"
vocab_path_inp = data_path + "Dataset/char_to_num_vocab_v2.pkl"



out_path = 'Dataset/'
vocab_path_out = out_path + "char_to_num_vocab_v2.pkl"



# Read metadata file and parse it
metadata_df = pd.read_csv(metadata_path, sep="\t")
# metadata_df.columns = ["file_name", "transcription", "normalized_transcription"]
metadata_df = metadata_df[["path", "sentence"]]
new_column_names = {'path': 'file_name', 'sentence':"normalized_transcription"}

# Rename columns using the .rename() method
metadata_df =metadata_df.rename(columns=new_column_names)
metadata_df = metadata_df.sample(frac=1).reset_index(drop=True)
# metadata_df = metadata_df.iloc[:500,:]
metadata_df["file_name"] = metadata_df["file_name"].apply(lambda x: x[:-4])
metadata_df = metadata_df[metadata_df['normalized_transcription'].str.len() <= 200]


maxl = 0
max_se = ""
pos1 = None
for pos,i in enumerate(metadata_df["normalized_transcription"]):
  if len(i)>maxl:
    maxl = len(i)
    max_se = i
    pos1 = pos
print(maxl,max_se)
# print(metadata_df.head(3))
# print(pos1)

125 کینیا کے دارلحکومت میں ربڑ اور پلاسٹک کے ڈھیر فوٹو گرافر ایڈورڈ برٹینسکی کی تصاویر پہلی بار دکھنے میں معمولی ضرور نظر آتی ہیں


In [7]:

print(len(metadata_df))
metadata_df.tail()

19999


file_name  \
19995  common_voice_ur_30677828   
19996  common_voice_ur_32037549   
19997  common_voice_ur_31809897   
19998  common_voice_ur_31935727   
19999  common_voice_ur_32016467   

                                normalized_transcription  
19995                  وہ رسیوں کو سانپ سمجھنے لگتے ہیں۔  
19996                   جیسا کہ تشدد، بم دھماکے اورجہاد۔  
19997                             یہ ضروری معلوم ہوتا ہے  
19998  جبکہ یہ معاملہ انفرادی نوعیت سے نکل کر اجتماعی...  
19999  پاکستان ترقی خوشحالی کی راہ پر گامزن ہے خرم دس...

In [8]:
split = int(len(metadata_df) * 0.90)
df_train = metadata_df[:split]
df_val = metadata_df[split:]

print(f"Size of the training set: {len(df_train)}")
print(f"Size of the training set: {len(df_val)}")


Size of the training set: 17999
Size of the training set: 2000


In [9]:
import pickle
from tensorflow import keras

# chars_vocab = {'’', 'ى', 'ُ', '”', 'ﷲ', 'ﷺ', 'ض', 'ؤ', '؟', 'ظ', 'ن', 'ﻧ', 'ﺗ', 'و', 'ؓ', 'ه', '`', 'ً', 'ﯾ', 'د', 'ؔ', 'ْ', 'ٰ', 'ﺲ', 'ل', 'ت', '"', 'ش', 'ی', ':', 'ک', "'", 'ء', 'م', 'ٔ', 'ہ', 'ے', 'ژ', 'ۂ', 'ِ', 'ح', 'گ', 'ﺩ', 'چ', 'ص', 'ڈ', 'ﭨ', 'ك', '“', 'ٓ', 'ٗ', ',', 'ي', 'پ', 'ڑ', 'ث', 'َ', 'ف', 'ﮯ', 'ع', 'ب', 'آ', 'ر', '۔', 'ا', 'ھ', 'س', 'ئ', 'ذ', '.', 'أ', '!', 'ز', 'ط', 'خ', 'ﮭ', '،', 'ٹ', 'ۃ', '-', 'ج', 'ﺘ', 'ق', '…', ' ', 'غ', 'ؑ', 'ۓ', '؛', 'ﻮ', '‘', 'ں', 'ّ'} 
# characters = list(chars_vocab)
# allow = ["?", " ", "!", "'"]
# alphas = "abcdefghijklmnopqrstuvwxyz"
# characters = [i for i in "".join(characters) if ((i.isalpha()) or (i in allow)) and (i not in alphas)]

# # Creating the character to integer mapping
# char_to_num = keras.layers.StringLookup(vocabulary=characters, oov_token="")
# # Saving the vocabulary using pickle
# with open(vocab_path_out, "wb") as f:
#     pickle.dump(char_to_num.get_vocabulary(), f)

# Loading the vocabulary back from pickle
loaded_vocab = None
with open(vocab_path_inp, "rb") as f:
    loaded_vocab = pickle.load(f)

# Creating the integer to character mapping using the loaded vocabulary
char_to_num = keras.layers.StringLookup(vocabulary=loaded_vocab, oov_token="")
num_to_char = keras.layers.StringLookup(vocabulary=loaded_vocab, oov_token="", invert=True)

print(
    f"The loaded vocabulary is: {num_to_char.get_vocabulary()} "
    f"(size ={num_to_char.vocabulary_size()})"
)
print(
    f"The loaded vocabulary is: {char_to_num.get_vocabulary()} "
    f"(size ={char_to_num.vocabulary_size()})"
)

The loaded vocabulary is: ['', 'ۂ', 'غ', 'ك', 'ظ', 'س', 'ے', 'ھ', 'ﷺ', 'ﮯ', 'ب', 'ٹ', 'پ', 'ا', 'چ', 'ﺘ', 'ذ', 'ض', 'ژ', 'ۓ', 'ر', 'ث', 'ﭨ', 'خ', 'ڈ', 'ط', 'ک', 'ء', 'آ', 'ۃ', 'ش', 'ع', ' ', 'ﻮ', 'م', 'ى', 'أ', 'ی', 'ق', 'ﺗ', 'ن', '!', 'ں', 'ڑ', 'ﮭ', 'گ', 'ت', 'د', 'ﺩ', 'ف', "'", 'ح', 'ل', 'ج', 'و', 'ﻧ', 'ﷲ', 'ه', 'ي', 'ہ', 'ؤ', 'ز', 'ﺲ', 'ص', 'ﯾ', 'ئ'] (size =66)
The loaded vocabulary is: ['', 'ۂ', 'غ', 'ك', 'ظ', 'س', 'ے', 'ھ', 'ﷺ', 'ﮯ', 'ب', 'ٹ', 'پ', 'ا', 'چ', 'ﺘ', 'ذ', 'ض', 'ژ', 'ۓ', 'ر', 'ث', 'ﭨ', 'خ', 'ڈ', 'ط', 'ک', 'ء', 'آ', 'ۃ', 'ش', 'ع', ' ', 'ﻮ', 'م', 'ى', 'أ', 'ی', 'ق', 'ﺗ', 'ن', '!', 'ں', 'ڑ', 'ﮭ', 'گ', 'ت', 'د', 'ﺩ', 'ف', "'", 'ح', 'ل', 'ج', 'و', 'ﻧ', 'ﷲ', 'ه', 'ي', 'ہ', 'ؤ', 'ز', 'ﺲ', 'ص', 'ﯾ', 'ئ'] (size =66)


In [10]:

# An integer scalar Tensor. The window length in samples.
frame_length = 256#600#256
# An integer scalar Tensor. The number of samples to step.
frame_step = 160#307#160
# An integer scalar Tensor. The size of the FFT to apply.
# If not provided, uses the smallest power of 2 enclosing frame_length.
fft_length = 384#650#384


def encode_single_sample(wav_file, label):
    ###########################################
    ##  Process the Audio
    ##########################################
    # 1. Read wav

    file = tf.io.read_file(wavs_path + wav_file+".wav")
    # 2. Decode the wav file
    audio, _ = tf.audio.decode_wav(file)
    audio = tf.squeeze(audio, axis=-1)
    # 3. Change type to float
    audio = tf.cast(audio, tf.float32)
    # 4. Get the spectrogram
    spectrogram = tf.signal.stft(
        audio, frame_length=frame_length, frame_step=frame_step, fft_length=fft_length
    )
    # 5. We only need the magnitude, which can be derived by applying tf.abs
    spectrogram = tf.abs(spectrogram)
    spectrogram = tf.math.pow(spectrogram, 0.5)
    # 6. normalisation
    means = tf.math.reduce_mean(spectrogram, 1, keepdims=True)
    stddevs = tf.math.reduce_std(spectrogram, 1, keepdims=True)
    spectrogram = (spectrogram - means) / (stddevs + 1e-10)
    ###########################################
    ##  Process the label
    ##########################################
    # 7. Convert label to Lower case
    label = tf.strings.lower(label)
    # 8. Split the label
    label = tf.strings.unicode_split(label, input_encoding="UTF-8")
    # 9. Map the characters in label to numbers
    label = char_to_num(label)
    # 10. Return a dict as our model is expecting two inputs
    return spectrogram, label

In [14]:
batch_size = 32
# Define the training dataset
train_dataset = tf.data.Dataset.from_tensor_slices(
    (list(df_train["file_name"]), list(df_train["normalized_transcription"]))
)
train_dataset = (
    train_dataset.map(encode_single_sample, num_parallel_calls=tf.data.AUTOTUNE)
    .padded_batch(batch_size)
    .prefetch(buffer_size=tf.data.AUTOTUNE)
)

# Define the validation dataset
validation_dataset = tf.data.Dataset.from_tensor_slices(
    (list(df_val["file_name"]), list(df_val["normalized_transcription"]))
)
validation_dataset = (
    validation_dataset.map(encode_single_sample, num_parallel_calls=tf.data.AUTOTUNE)
    .padded_batch(batch_size)
    .prefetch(buffer_size=tf.data.AUTOTUNE)
)
for i in train_dataset.take(2):
    print(i[0].shape,i[1].shape)
print(len(metadata_df))

NotFoundError: {{function_node __wrapped__IteratorGetNext_output_types_2_device_/job:localhost/replica:0/task:0/device:CPU:0}} NewRandomAccessFile failed to Create/Open: ../Dataset/cv-corpus-14.0-2023-06-23/ur/limited_wav_files/limited_wav_files/common_voice_ur_26703970.wav : The system cannot find the path specified.
; No such process
	 [[{{node ReadFile}}]] [Op:IteratorGetNext]

In [13]:
for i in train_dataset.take(1):
  print(i[1][1])
  tf.strings.reduce_join(num_to_char(i[1][1])).numpy().decode("utf-8")

NotFoundError: {{function_node __wrapped__IteratorGetNext_output_types_2_device_/job:localhost/replica:0/task:0/device:CPU:0}} NewRandomAccessFile failed to Create/Open: ../Dataset/cv-corpus-14.0-2023-06-23/ur/limited_wav_files/limited_wav_files/common_voice_ur_26703970.wav : The system cannot find the path specified.
; No such process
	 [[{{node ReadFile}}]] [Op:IteratorGetNext]

In [14]:
# fig = plt.figure(figsize=(8, 5))
# for batch in train_dataset.take(1):
#     spectrogram = batch[0][0].numpy()
#     spectrogram = np.array([np.trim_zeros(x) for x in np.transpose(spectrogram)])
#     label = batch[1][0]
#     # Spectrogram
#     label = tf.strings.reduce_join(num_to_char(label)).numpy().decode("utf-8")
#     ax = plt.subplot(2, 1, 1)
#     ax.imshow(spectrogram, vmax=1)
#     ax.set_title(label)
#     ax.axis("off")
#     # Wav
#     file = tf.io.read_file(wavs_path + list(df_train["file_name"])[0] + ".wav")
#     audio, _ = tf.audio.decode_wav(file)
#     audio = audio.numpy()
#     ax = plt.subplot(2, 1, 2)
#     plt.plot(audio)
#     ax.set_title("Signal Wave")
#     ax.set_xlim(0, len(audio))
#     display.display(display.Audio(np.transpose(audio), rate=30000))
# plt.show()

In [15]:

def CTCLoss(y_true, y_pred):
    # Compute the training-time loss value
    batch_len = tf.cast(tf.shape(y_true)[0], dtype="int64")
    input_length = tf.cast(tf.shape(y_pred)[1], dtype="int64")
    label_length = tf.cast(tf.shape(y_true)[1], dtype="int64")

    input_length = input_length * tf.ones(shape=(batch_len, 1), dtype="int64")
    label_length = label_length * tf.ones(shape=(batch_len, 1), dtype="int64")

    loss = keras.backend.ctc_batch_cost(y_true, y_pred, input_length, label_length)
    return loss

# def CTCLoss(y_true, y_pred):
#     label_length = tf.reduce_sum(tf.ones_like(y_true), axis=-1)
#     input_length = tf.reduce_sum(tf.ones_like(y_pred), axis=-1)
#     batch_len = tf.cast(tf.shape(y_true)[0], dtype="int64")

#     loss = keras.backend.ctc_batch_cost(y_true, y_pred, input_length, label_length)

#     return loss


In [16]:
# tpu = tf.distribute.cluster_resolver.TPUClusterResolver.connect()

# # instantiate a distribution strategy
# tpu_strategy = tf.distribute.experimental.TPUStrategy(tpu)

In [17]:
# # detect and init the TPU
# tpu = tf.distribute.cluster_resolver.TPUClusterResolver.connect()
# tpu_strategy = tf.distribute.experimental.TPUStrategy(resolver)
# # instantiate a distribution strategy
# tpu_strategy = tf.distribute.experimental.TPUStrategy(tpu)

In [18]:

def build_model(input_dim, output_dim, rnn_layers=5, rnn_units=128):
    """Model similar to DeepSpeech2."""
    # Model's input
    input_spectrogram = layers.Input((None, input_dim), name="input")
    # Expand the dimension to use 2D CNN.
    x = layers.Reshape((-1, input_dim, 1), name="expand_dim")(input_spectrogram)
    # Convolution layer 1
    x = layers.Conv2D(
        filters=32,
        kernel_size=[11, 41],
        strides=[2, 2],
        padding="same",
        use_bias=False,
        name="conv_1",
    )(x)
    x = layers.BatchNormalization(name="conv_1_bn")(x)
    x = layers.ReLU(name="conv_1_relu")(x)
    # Convolution layer 2
    x = layers.Conv2D(
        filters=32,
        kernel_size=[11, 21],
        strides=[1, 2],
        padding="same",
        use_bias=False,
        name="conv_2",
    )(x)
    x = layers.BatchNormalization(name="conv_2_bn")(x)
    x = layers.ReLU(name="conv_2_relu")(x)
    # Reshape the resulted volume to feed the RNNs layers
    x = layers.Reshape((-1, x.shape[-2] * x.shape[-1]))(x)
    # RNN layers
    for i in range(1, rnn_layers + 1):
        recurrent = layers.GRU(
            units=rnn_units,
            activation="tanh",
            recurrent_activation="sigmoid",
            use_bias=True,
            return_sequences=True,
            reset_after=True,
            name=f"gru_{i}",
        )
        x = layers.Bidirectional(
            recurrent, name=f"bidirectional_{i}", merge_mode="concat"
        )(x)
        if i < rnn_layers:
            x = layers.Dropout(rate=0.5)(x)
    # Dense layer
    x = layers.Dense(units=rnn_units * 2, name="dense_1")(x)
    x = layers.ReLU(name="dense_1_relu")(x)
    x = layers.Dropout(rate=0.5)(x)
    # Classification layer
    output = layers.Dense(units=output_dim + 1, activation="softmax")(x)
    # Model
    model = keras.Model(input_spectrogram, output, name="DeepSpeech_2")
    # Optimizer
    opt = keras.optimizers.Adam(learning_rate=1e-4)
    # Compile the model and return
    model.compile(optimizer=opt, loss=CTCLoss)
    return model


# Get the model
# instantiating the model in the strategy scope creates the model on the TPU
# with tpu_strategy.scope():
model = build_model(
    input_dim=fft_length // 2 + 1,
    output_dim=char_to_num.vocabulary_size(),
    rnn_units=512,
)
model.summary(line_length=110)

Model: "DeepSpeech_2"


______________________________________________________________________________________________________________


 Layer (type)                                    Output Shape                                Param #          


 input (InputLayer)                              [(None, None, 193)]                         0                


 expand_dim (Reshape)                            (None, None, 193, 1)                        0                


...

 dense (Dense)                                   (None, None, 67)                            68675            


Total params: 26,664,355


Trainable params: 26,664,227


Non-trainable params: 128


______________________________________________________________________________________________________________


In [19]:


# A utility function to decode the output of the network
def decode_batch_predictions(pred):
    input_len = np.ones(pred.shape[0]) * pred.shape[1]
    # Use greedy search. For complex tasks, you can use beam search
    results = keras.backend.ctc_decode(pred, input_length=input_len, greedy=True)[0][0]
    # Iterate over the results and get back the text
    output_text = []
    for result in results:
        result = tf.strings.reduce_join(num_to_char(result)).numpy().decode("utf-8")
        output_text.append(result)
    return output_text


# A callback class to output a few transcriptions during training
class CallbackEval(keras.callbacks.Callback):
    """Displays a batch of outputs after every epoch."""
    print("CallbackEval")
    def __init__(self, dataset):
        super().__init__()
        self.dataset = dataset

    def on_epoch_end(self, epoch: int, logs=None):
        predictions = []
        targets = []
        for batch in self.dataset:
            X, y = batch
            batch_predictions = model.predict(X)
            batch_predictions = decode_batch_predictions(batch_predictions)
            predictions.extend(batch_predictions)
            for label in y:
                label = (
                    tf.strings.reduce_join(num_to_char(label)).numpy().decode("utf-8")
                )
                targets.append(label)
        wer_score = wer(targets, predictions)
        print("-" * 100)
        print(f"Word Error Rate: {wer_score:.4f}")
        print("-" * 100)
        for i in np.random.randint(0, len(predictions), 2):
            print(f"Target    : {targets[i]}")
            print(f"Prediction: {predictions[i]}")
            print("-" * 100)




CallbackEval


In [20]:
!cp /kaggle/input/urdu-dataset-20000/model_checkpoint_v2.h5 /kaggle/working/

In [21]:
# Define the number of epochs.
epochs = 30
# Callback function to check transcription on the val set.
validation_callback = CallbackEval(validation_dataset)
# Train the model
from keras.callbacks import ModelCheckpoint

# Define file paths for model checkpoints
model_checkpoint_path = "/kaggle/working/model_checkpoint_v2.h5"
# model_weights_path = "model_weights.h5"

# Define checkpoint callback
checkpoint_callback = ModelCheckpoint(
    filepath=model_checkpoint_path,
    save_best_only=False,  # Save the model on every epoch
    save_weights_only=False,  # Save the entire model (including architecture)
    verbose=1
)

# checkpoint_callback = tf.keras.callbacks.ModelCheckpoint(
#         filepath=model_checkpoint_path,
#         verbose=1,
#         save_weights_only=True,
#         # save_freq=5*batch_size
#         )


# ... (your existing code)

# Load the model if a checkpoint exists
if os.path.exists(model_checkpoint_path):
    # model = keras.models.load_model(model_checkpoint_path)
    custom_objects = {"CTCLoss": CTCLoss}
    with keras.utils.custom_object_scope(custom_objects):
        model = keras.models.load_model(model_checkpoint_path)

# Training loop

model.fit(
    train_dataset,
    epochs=epochs,
    callbacks=[checkpoint_callback, CallbackEval(validation_dataset)],
    # ... other training configurations
)
# 3 epochs - loss: 113.3001




Epoch 1/30



  1/563 [..............................] - ETA: 6:24:52 - loss: 49.4535


  2/563 [..............................] - ETA: 2:06:26 - loss: 40.2359


  3/563 [..............................] - ETA: 2:19:01 - loss: 40.1282


  4/563 [..............................] - ETA: 2:09:36 - loss: 37.8915

...


181/563 [========>.....................] - ETA: 18:59 - loss: 16.5713


182/563 [========>.....................] - ETA: 18:56 - loss: 16.5723


183/563 [========>.....................] - ETA: 18:51 - loss: 16.5687


184/563 [========>.....................] - ETA: 18:49 - loss: 16.6232


185/563 [========>.....................] - ETA: 18:46 - loss: 16.6500

In [ ]:
for batch in validation_dataset:
    X, y = batch
    pred = model.predict(X)

#     print(pred[1][1],pred[1].shape,pred[1][1].shape)
    input_len = np.ones(pred.shape[0]) * pred.shape[1]
    # Use greedy search. For complex tasks, you can use beam search
    results = keras.backend.ctc_decode(pred, input_length=input_len, greedy=True)[0][0]
    print("*********************************")
#     print(results[0],results.shape)
    # Iterate over the results and get back the text
    output_text = []
    for result in results:
        result = tf.strings.reduce_join(num_to_char(result)).numpy().decode("utf-8")
        output_text.append(result)
    print("----------------------------------------")
    print(output_text,len(output_text))
    break



In [ ]:
# # Let's check results on more validation samples
# predictions = []
# targets = []
# for batch in validation_dataset:
#     X, y = batch
#     batch_predictions1 = model.predict(X)
#     print(batch_predictions1[:2])
#     batch_predictions = decode_batch_predictions(batch_predictions1)
#     print(batch_predictions,len(batch_predictions))
#     predictions.extend(batch_predictions)
#     for label in y:
#         label = tf.strings.reduce_join(num_to_char(label)).numpy().decode("utf-8")
#         targets.append(label)
# wer_score = wer(targets, predictions)
# print("-" * 100)
# print(f"Word Error Rate: {wer_score:.4f}")
# print("-" * 100)
# for i in np.random.randint(0, len(predictions), 5):
#     print(f"Target    : {targets[i]}")
#     print(f"Prediction: {predictions[i]}")
#     print("-" * 100)
# predicted = pd.DataFrame()
# predicted["predictions"]= predictions
# predicted["Target"] = targets

In [ ]:
# predicted.head(20)

PRedicrt Wave.py


In [18]:
import os
import tensorflow as tf
from tensorflow import keras
from keras.callbacks import ModelCheckpoint
from load_dataset import Load_Data
from preprocess import Preporcess_Data
from utils import decode_batch_predictions,CTCLoss

model_checkpoint_path = "../models/model_checkpoint_v2.h5"

load_data = Load_Data(data_path="../",out_path="../",predict=True)
char_to_num= load_data.char_to_num
num_to_char  = load_data.num_to_char
wavs_path =load_data.wavs_path


prepro_data = Preporcess_Data(wavs_path,char_to_num,predict=True)


# Define checkpoint callback
checkpoint_callback = ModelCheckpoint(
    filepath=model_checkpoint_path,
    save_best_only=False,  # Save the model on every epoch
    save_weights_only=False,  # Save the entire model (including architecture)
    verbose=1
)



# Load the model if a checkpoint exists
if os.path.exists(model_checkpoint_path):
    # model = keras.models.load_model(model_checkpoint_path)
    custom_objects = {"CTCLoss": CTCLoss}
    with keras.utils.custom_object_scope(custom_objects):
        model = keras.models.load_model(model_checkpoint_path)


def take_input():
    int1 = input("Enter audio file name:")
    return int1
# a = True
while True:
    wav_file  =  take_input()
    if wav_file == "":
        # a = False
        break
    # validation_dataset = tf.data.Dataset.from_tensor_slices(
    # wav_file )
 
    spectograms = prepro_data.encode_single_sample(wav_file)

    # Let's check results on more validation samples
    predictions = []
    #reshape spectograms (1,spectograms.shape[0],spectograms.shape[1])
    spectograms=tf.expand_dims(spectograms, axis=0)
    print("Spectogram shape: ",spectograms.shape)
    # spectograms = tf.expand_dims(spectograms, axis=0)
    batch_predictions1 = model.predict(spectograms)
    # print(batch_predictions1[:2])
    batch_predictions = decode_batch_predictions(batch_predictions1,num_to_char)
    print(batch_predictions,len(batch_predictions))
# Enter audio file name:common_voice_ur_26562732.wav





#common_voice_ur_26562732,common_voice_ur_26562733


Spectogram shape:  (1, 467, 193)
1/1 [==============================] - 13s 13s/step
['دلچسپ کمریہ ہے'] 1
Spectogram shape:  (1, 467, 193)
1/1 [==============================] - 4s 4s/step
['دلچسپ کمریہ ہے'] 1
Spectogram shape:  (1, 705, 193)
1/1 [==============================] - 10s 10s/step
['وقت پر رقوم کبھی بھی واپٹ نہ کیں'] 1
